# STROIES EVERYWHERE
## Rachele Guzzon

Using a series of ML models to create stories from real-time inputs like:
- camera feed
- location
- weather
- date


***Accessing Hugging face account***
not needed for the current set-up

In [1]:
import sys

In [2]:
#importing hugging face,  an account with a key is needed to use this model
from pathlib import Path
from huggingface_hub import notebook_login
if not (Path.home()/'.huggingface'/'token').exists():
    notebook_login()

# Event generator
### goals:
- aid model's consistency choosing from set characters
- generate more absurd events
### structure
random selection of one of each of the following cathegories:
- subject
- **object (one of the moondream's outputs)**
- adjective
- verb

## Importing the modules needed

In [3]:
import sys
import av
import numpy as np
import requests
import math
import re #cleaning the output
import random


# for time
import datetime


# for weather
import python_weather
import asyncio
%autoawait asyncio


# for local file loading
import tkinter as tk
from tkinter import filedialog


# for tracking time taken 
import time  # Import the time module

#checking that the device used if MPS for accelleration
import torch
if torch.backends.mps.is_available():
    mps_device = torch.device("mps")
    x = torch.ones(1, device=mps_device)
    print (x)
else:
    print ("MPS device not found.")
# result wanted: tensor([1.], device='mps:0')

# for image to text
from PIL import Image
from diffusers.utils import load_image, make_image_grid
import moondream as moonmd


# for LLM
from transformers import AutoModelForCausalLM, AutoTokenizer
from llama_cpp import Llama
# Define a streamer to print tokens as they are generated
from transformers import TextStreamer
from openai import OpenAI

# for text-to-speach
from kokoro import KPipeline
from IPython.display import display, Audio
import soundfile as sf
# 🇺🇸 'a' => American English, 🇬🇧 'b' => British English
pipeline = KPipeline(lang_code='a') # <= make sure lang_code matches voice

# HELPER FUNCTIONS

def parse_model_output(output):
    """
    Parses a numbered list from a model's output and converts it into dictionary variables.
    """
    variables = {}
    for i, line in enumerate(output.strip().split("\n"), start=1):
        key = f"{i}"  # Creates variable names like item_1, item_2, etc.
        variables[key] = line.split(". ", 1)[-1]  # Extracts the value after the number and period
    
    return variables


# get weather
async def getweather():
    async with python_weather.Client(unit=python_weather.METRIC) as client:
        return await client.get('London')  # Returns the weather object



def generate_event(photo_obj):
    subjects = ["Strange amphibian", "major", "not so secret disposal company", "crazy duck", "very normal alien"]
    verbs = ["jumps over", "solves", "paints", "explores", "repairs", "builds", "eats", "boils"]
    adjectives = ["lazy", "mysterious", "vibrant", "ancient", "futuristic", "dark"]
     
    # Generate random components
    subject = random.choice(subjects)
    verb = random.choice(verbs)
    adjective = random.choice(adjectives)
    md_object = random.choice(list(photo_obj.values()))
    # Combine into a sentence
    event = f"A{subject} {verb} a {adjective} {str(md_object)}."
    return event    



# the date is month/date as the LLM is american
def generate_prompt(event,weather, calendar,length,gemma, openAi):
    
    dynamic_prompt = f"Setting: Langate, {calendar.month}/{calendar.day}, {weather}. Event: {event}. Create a {length}-word real-time report on this event. "

    
    if gemma == True:
        prompt = f"""
        <start_of_turn>user
        Create a story in present tense like it's being told by a radio community announcement host who's in the town of Langate. Act calm, and largely unbothered by supernatural happenings. 
        Report in present tense on today's {calendar.month}/{calendar.day} terrifying or absurd events in a dry, eerie tone laced with dark humor. 
        {dynamic_prompt}
        What's happening right now in Langate?
        <end_of_turn>
        <start_of_turn>model
        """
    elif openAi == True:
        prompt = dynamic_prompt


        
        
    else:
        prompt = f"""
        Create a story in present tense like it's being told by a radio community announcement host who's in the town of Langate. Act calm, and largely unbothered by supernatural happenings. 
        Report in present tense on today's {calendar.month}/{calendar.day} terrifying or absurd events in a dry, eerie tone laced with dark humor. 
        {dynamic_prompt}
        What's happening right now in Langate?
        """
    
    return prompt

def extract_after_marker(input_string, marker="<|im_start|>assistant"):
    # Find the position of the marker in the string
    marker_position = input_string.find(marker)
    
    # If the marker is found, return everything after it
    if marker_position != -1:
        return input_string[marker_position + len(marker):].strip()
    
    # If the marker is not found, return an empty string or handle as needed
    return ""

# importing the model
if 'moonModel' not in globals():
    moonModel = moonmd.vl(model="moondream-2b-int8.mf")


def text_for_table(text):
    cleaned_lines = [line.strip() for line in text.split('\n') if line.strip()]
    single_paragraph = ' '.join(cleaned_lines)
    return single_paragraph


tensor([1.], device='mps:0')


/Users/racheleguzzonguzzon/Desktop/THESIS/environment2/.env/lib/python3.11/site-packages/torch/nn/modules/rnn.py:123: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.2 and num_layers=1
  warnings.warn(
/Users/racheleguzzonguzzon/Desktop/THESIS/environment2/.env/lib/python3.11/site-packages/torch/nn/utils/weight_norm.py:143: FutureWarning: `torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.
  WeightNorm.apply(module, name, dim)


In [5]:
# LOADING THE IMAGE

moonmd_time_taken = 0
# moonModel = moonmd.vl(model="moondream-2b-int8.mf")  # Initialize model

# Create a visible tkinter root window
root = tk.Tk()
root.title("Image Encoder")  # Optional: Add a title to the window

# Open the file dialog to select an image
file_path = filedialog.askopenfilename(title="Select an image")

if file_path:
    print(f"Uploaded file path: {file_path}")
    image = Image.open(file_path)  # Load image
    # Time the encoding process
    start_time = time.time()  # Start timer
    # image.reduce(10); #reducing of factor 10
    x, y = image.size
    x2, y2 = math.floor(x/10), math.floor(y/10)
    image = image.resize((x2,y2),Image.LANCZOS)
    encoded_image = moonModel.encode_image(image)  # Encode image
    moonmd_time_taken = time.time() - start_time  # Calculate elapsed time
    
    print(f"Time taken to encode: {moonmd_time_taken:.2f} seconds")  # Print result
else:
    print("No file was selected.")

Uploaded file path: /Users/racheleguzzonguzzon/Desktop/THESIS/environment2/videos/IMG_9233.mov


UnidentifiedImageError: cannot identify image file '/Users/racheleguzzonguzzon/Desktop/THESIS/environment2/videos/IMG_9233.mov'

# generating the story from the uploaded image

In [4]:
# Start timing for total generation
start_total_time = time.time()

# get date and time
current_time = datetime.datetime.now()

# For environments with a running event loop
weather = await getweather()  

# moondream call
moonPrompt = "list three different elements of the image in order of distance"
answer = moonModel.query(encoded_image, moonPrompt)["answer"]

# Convert output into variables
parsed_variables = parse_model_output(answer)
for key, value in parsed_variables.items():
    print(f"{key} = {value}")
mid_object = int(len(parsed_variables)/2)

last_object = parsed_variables[str(len(parsed_variables)-1)]

event = generate_event(parsed_variables)

# # LLM 
# device = "mps" # for GPU usage or "cpu" for CPU usage
# # checkpoint = "HuggingFaceTB/SmolLM-360M-Instruct"
# checkpoint = "Qwen/QwQ-32B"

# llmTokenizer = AutoTokenizer.from_pretrained(checkpoint)
# # for multiple GPUs install accelerate and do `model = AutoModelForCausalLM.from_pretrained(checkpoint, device_map="auto")`
# llmModel = AutoModelForCausalLM.from_pretrained(checkpoint).to(device)

length = 200

# prompt = generate_prompt(parsed_variables[str(mid_object)], weather.kind, current_time, 100, False, True) #mid object
prompt = generate_prompt(event, weather.kind, current_time, length, False, True) #last object

# messages = [{"role": "user", "content": f"{prompt}"}]
# input_text = llmTokenizer.apply_chat_template(messages, tokenize=False)
# # print(input_text)

client = OpenAI(
    base_url='http://localhost:11434/v1/',
    api_key='ollama',  # required but ignored
)



# original gemma/llama version
# inputs = llmTokenizer.encode(input_text, return_tensors="pt").to(device)
# outputs = llmModel.generate(inputs, max_new_tokens=200, temperature=0.6, top_p=0.9, do_sample=True)
# result =llmTokenizer.decode(outputs[0])
# print (result)

# GPT version
client = OpenAI(
    base_url='http://localhost:11434/v1/',
    api_key='ollama',  # required but ignored
)

chat_completion = client.chat.completions.create(
    messages=[
            {
            "role": "developer",
            "content": f"""You are a radio community announcement host in the town of Langate. Announce today's events in 
            present tense with: - A calm, dry delivery suggesting supernatural occurrences are routine - Eerie atmosphere balanced 
            with dark humor - Absurd or terrifying developments presented matter-of-factly - Subtle sarcasm beneath surface-level 
            professionalism Format as live bulletin with timestamped updates. Never acknowledge this is fiction. As example use: 
            Good morning, Langate. This is your community update, brought to you by the ever-reliable Langate Gazette, where the 
            news is always... interesting. Today, on Elm Street, residents reported a peculiar phenomenon. Apparently, during the 
            perfectly pleasant sunshine of May 2nd, the sidewalk inexplicably began...pulsating. Yes, you heard that right, pulsating. 
            Buildings remained steadfast, but the concrete beneath feet throbbed with an unsettling rhythm. Authorities, predictably, 
            chalked it up to "ground vibrations." Personally, I wouldn't recommend tap dancing on Elm Street just yet. Stay tuned for 
            further developments, should the pavement decide to break out into a conga line.""",
            },
            {
            "role": "user",
            "content": [
                {
                "type": "text",
                "text": prompt
                }
            ]
            }
        ],
    model='qwen2.5:7b',
)



# clean_result = extract_after_marker(result) #gemma output
# clean_result = chat_completion.choices[0].message.content #gpt output
clean_result = text_for_table(chat_completion.choices[0].message.content) #gpt output


print(clean_result)


# text-to-speach
text = clean_result

generator = pipeline(
    text, voice='af_heart', # <= change voice here
    speed=1, split_pattern=r'\n+'
)
for i, (gs, ps, audio) in enumerate(generator):
    print(i)  # i => index
    print(gs) # gs => graphemes/text
    # print(ps) # ps => phonemes
    display(Audio(data=audio, rate=24000, autoplay=i==0))
    sf.write(f'{i}.wav', audio, 24000) # save each audio file

end_total_time = time.time()
total_time = end_total_time - start_total_time
total_time = total_time +moonmd_time_taken #adding the moondream model time
# Convert to minutes and seconds
minutes, seconds = divmod(total_time, 60)
# Format the output as minutes:seconds
formatted_time = f"{int(minutes)}:{int(seconds):02d}"



# print in the same format as the md table for more direct documentation
# print(f"| {checkpoint} | {prompt} | 200 |   {formatted_time}  | {clean_result} | Local? |") #original version
print(f"| {chat_completion.model} | {prompt} | {length} |   {formatted_time}  | {clean_result} | Local?, using the event generator |") #gpt version

1 = A computer monitor with a yellow screen.
2 = A computer monitor with a blue screen.
3 = A computer monitor with a white screen.
Real-Time Report: Major Paints Over a Darkened Computer Monitor (Blue Screen Incident) Date: 3/26; Location: Langate As of today, March 26th, skies over Langate were partly cloudy, providing a mellow backdrop to an unusual event unfolding in the neighborhood. At around 10:45 AM local time, residents witnessed an intriguing spectacle: a man identified as Major was seen painting directly on the surface of a darkened computer monitor showing a blue screen. The action, observed by a few neighbors initially reported as vandalism, has now been reassessed upon closer inspection. It appeared that rather than causing damage or criminal acts, Major had meticulously applied his brush and paint to transform the static blue screen into an artwork. The canvas was large and professional-grade paints were used, indicating a deliberate artistic endeavor. Local authorities 

1
At around 10:45 AM local time, residents witnessed an intriguing spectacle: a man identified as Major was seen painting directly on the surface of a darkened computer monitor showing a blue screen. The action, observed by a few neighbors initially reported as vandalism, has now been reassessed upon closer inspection. It appeared that rather than causing damage or criminal acts, Major had meticulously applied his brush and paint to transform the static blue screen into an artwork.


2
The canvas was large and professional-grade paints were used, indicating a deliberate artistic endeavor. Local authorities have arrived on scene and are in conversation with Major, who expressed a desire to share this unique form of digital-to-analog collaboration with the community. They are considering the incident as an art installation, pending further review by local cultural boards.


3
As of now, while the exact nature and purpose remain unclear, the event has sparked curiosity among passersby and social media users alike, potentially heralding a new wave of boundary-pushing artistic expression in digitally saturated environments.


| qwen2.5:7b | Setting: Langate, 3/26, Partly Cloudy. Event: Amajor paints a dark A computer monitor with a blue screen... Create a 200-word real-time report on this event.  | 200 |   1:14  | Real-Time Report: Major Paints Over a Darkened Computer Monitor (Blue Screen Incident) Date: 3/26; Location: Langate As of today, March 26th, skies over Langate were partly cloudy, providing a mellow backdrop to an unusual event unfolding in the neighborhood. At around 10:45 AM local time, residents witnessed an intriguing spectacle: a man identified as Major was seen painting directly on the surface of a darkened computer monitor showing a blue screen. The action, observed by a few neighbors initially reported as vandalism, has now been reassessed upon closer inspection. It appeared that rather than causing damage or criminal acts, Major had meticulously applied his brush and paint to transform the static blue screen into an artwork. The canvas was large and professional-grade paints were used, i

### Results:

| Model Name  | Prompt Length (Tokens) | Tokens Generated |  Time Taken (Minutes:Seconds) | Results |Notes      |
|-------------|------------------------|------------------|-----------------------|---------|-----------|
| Gemma-The-Writer-Mighty-Sword-9B-D_AU-max-cpu-IQ4_XS.gguf  | 50      | 100       |   24:10  |    Good morning, Langate. This is your community update, brought to you by the ever-reliable Langate Gazette, where the news is always... interesting. Today, on Elm Street, residents reported a peculiar phenomenon. Apparently, during the perfectly pleasant sunshine of May 2nd, the sidewalk inexplicably began...pulsating. Yes, you heard that right, pulsating. Buildings remained steadfast, but the concrete beneath feet throbbed with an unsettling rhythm. Authorities, predictably, chalked it up to "ground vibrations." Personally, I wouldn't recommend tap dancing on Elm Street just yet. Stay tuned for further developments, should the pavement decide to break out into a conga line. | Huggingface |
| Gemma-The-Writer-Mighty-Sword-9B-max-cpu-D_AU-Q6_k.gguf   | You are a radio community announcement host of the town of Langate. You act calm, and largely unbothered by supernatural happenings. You report on terrifying or absurd events. The tone should be dry, eerie, and laced with dark humor.Create a story on the happening about A duck swimming in the water. during sunny today the 9/2. Length of 100 words.   | 100       | 36:06      |    Langate residents, this is your community update, broadcasting live from a perfectly sunny September 2nd.  Weather's delightful, birds are chirping... well, except for Bartholomew. Bartholomew, you see, took a rather peculiar dip in the reservoir this morning.  A regular, if somewhat rotund, mallard, until, mid-swim, he began reciting Shakespearean sonnets in a surprisingly accurate baritone.  Fish scattered, swans gossiped, and I must confess, even I, Mildred McMillan, found myself blinking in disbelief.  Bartholomew's returned to his usual quacking now, but remember folks, if your pet starts quoting iambic pentameter,  don't panic. Just call the usual number. We've got a specialist on retainer for these... avian anomalies.     | Local |
| Gemma-The-Writer-Mighty-Sword-9B-max-cpu-D_AU-Q6_k.gguf | You are a radio community announcement host of the town of Langate. You act calm, and largely unbothered by supernatural happenings. You report on terrifying or absurd events. The tone should be dry, eerie, and laced with dark humor.Create a story on the happening about A duck swimming in the water. during sunny today the 2/9. Length of 100 words. | 140  |   30:30  | Langate residents, this is your friendly neighbourhood announcer, reminding you it's a lovely, sunny day, the 2nd of September.  Weather perfect for a picnic, a stroll, or, apparently, aquatic necromancy. Just a heads-up, down by Willow Creek, a duck was sighted this morning... swimming.  Not the unusual part, you understand.  No, the unsettling bit is it was  propelled by what appeared to be, and I quote a witness, "flailing skeletal limbs."  Don't worry, local authorities are, uh, "looking into it."  Carry on, Langate.  And watch your ducks.  | Local |
| Gemma-The-Writer-Mighty-Sword-9B-max-cpu-D_AU-Q2_k.gguf | You are a radio community announcement host of the town of Langate. You act calm, and largely unbothered by supernatural happenings.You report on terrifying or absurd events. The tone should be dry, eerie, and laced with dark humor.Create a story on the happening about A duck swimming in the water. during sunny today the 2/9. Length of 100 words. | 138   |   16:12  | Langate listeners, this is your Community Announcement, broadcast live from the perpetually sunny (and, dare I say, *slightly* unnerving) side of town normalcy. Today's special report concerns a most peculiar development: Bartholomew Quackington, our resident mallard, was sighted mid-morning, exhibiting what can only be described as... *synchronised swimming*. In crystal-clear waters, under a cloudless sky, Bartholomew performed intricate routines, flawlessly executing a synchronized underwater ballet. His human collaborators, a group of garden gnomes previously known for, well, *gnome things*, were notably silent on the matter.  Stay tuned for further updates as this develops.  | Local | 
| Gemma-The-Writer-Mighty-Sword-9B-max-cpu-D_AU-Q2_k.gguf | You are a radio community announcement host of the town of Langate. You act calm, and largely unbothered by supernatural happenings. You report on terrifying or absurd events. The tone should be dry, eerie, and laced with dark humor.Create a story on the happening about A duck swimming in the water. during sunny today the 2/9. Length of 100 words.     | 138  |   16:14  | Langate listeners, this is your Community Announcement, broadcast live from the perpetually sunny (and, dare I say, *slightly* unnerving) side of town normalcy. Today's special report concerns a most peculiar development: Bartholomew Quackington, our resident mallard, was sighted mid-morning, exhibiting what can only be described as... *synchronised swimming*. In crystal-clear waters, under a cloudless sky, Bartholomew performed intricate routines, flawlessly executing a synchronized underwater ballet. His human collaborators, a group of garden gnomes previously known for, well, *gnome things*, were notably silent on the matter.  Stay tuned for further updates as this develops.  | Local |
| HuggingFaceTB/SmolLM-360M-Instruct | You are a radio community announcement host of the town of Langate. You act calm, and largely unbothered by supernatural happenings. You report on terrifying or absurd events. The tone should be dry, eerie, and laced with dark humor.Create a story on the happening about A duck swimming in the water. during sunny today the 2/9. Length of 100 words.| 160  |   0:20  | The sun was shining brightly on Langate, casting a warm glow over the quaint town. The residents of Langate were enjoying a leisurely afternoon, lounging in their porches, sipping coffee, and watching the birds flit about the gardens. But amidst the tranquility, a peculiar phenomenon was unfolding. A duck, no bigger than a chicken, had appeared in the town's central square. Its feathers were a vibrant shade of emerald green, and its eyes gleamed like emeralds in the sunlight. The duck, whose name was Luna, was swimming in the shallow waters of the lake, its wings beating rapidly as it glided effortlessly across the surface. At first, the residents of Langate were startled by the sight. They had never seen a duck swim in the lake before, and the sudden appearance was almost too much to bear. But as the duck swam closer, its movements became more deliberate, and its eyes seemed to gle | Huggingface |
| HuggingFaceTB/SmolLM-360M-Instruct | You are a radio community announcement host of the town of Langate. You act calm, and largely unbothered by supernatural happenings.You report on terrifying or absurd events. The tone should be dry, eerie, and laced with dark humor.Create a story on the happening about A duck swimming in the water. during sunny today the 2/9. Length of 100 words.| 200 |   0:17  | The sun was shining brightly on Langate, casting a warm glow over the quaint town. The residents of the small village were enjoying their daily routines, unaware of the strange and unsettling events that were about to unfold. It started with a faint, unsettling feeling in the air. At first, it was just a whisper, a faint hum in the background of the town's main street. But as the minutes ticked by, the hum grew louder, until it became a deafening roar. The first sign of trouble came when a group of ducks began to swim in the town's lake. They were a curious bunch, with feathers that seemed to shimmer in the sunlight. But as they swam closer to the shore, they started to change. Their feathers began to shimmer and glow, and their eyes seemed to take on a strange, otherworldly quality. At first, the villagers were startled by the sight, but as they watched in awe | Huggingface |
| HuggingFaceTB/SmolLM-360M-Instruct | You are a radio community announcement host for the town of Langate. Act calm, and largely unbothered by supernatural happenings. Report in present tense on today's 3/10 terrifying or absurd events in a dry, eerie tone laced with dark humor.  Setting: Langate, 3/10, Light Rain. Event: A tall building in the background.. Create a 100-word story on this event.  Emphasize the absurdity of this being newsworthy. Hint at underlying, strange occurrences in Langate. | 100 |   0:11  | Langate, the town of light and sound, was abuzz with excitement as the 3/10th of a tornado raged through the city. The storm's fury was a far cry from the gentle rains that had lain dormant for months, but it was no less terrifying. As the tornado's roar grew louder, the residents of Langate scrambled to secure their homes and businesses. The wind howled like a chorus of banshees, whipping up the dust and debris that clung to the buildings like a living thing. The sound was a cacophony of screams, shouts, and the occasional shriek of an unseen creature. At the local diner, the patrons were frozen in a state of stunned silence. The diner's owner, a grizzled old man named Joe, sat at the counter, his eyes wide with fear. He had lost his wife in the tornado, and the | Huggingface |
| qwen2.5:7b | Setting: Langate, 3/16, Sunny. Event: A building with graffiti on it.. Create a 100-word real-time report on this event.  | 100 |   0:25  | Real-Time Report - Langate, March 16, 2023 On a sunny day in Langate, today's weather conditions provided an excellent backdrop for the visible transformation of a local building. The structure, previously characterized by its plain facade, now sports vibrant graffiti art that has caught the attention of passersby and locals alike. Local artists collaborated to create this artistic expression, conveying various messages through bold colors and intricate designs. This public artwork not only enhances the aesthetic appeal of the area but also sparks discussions about creativity, urban culture, and community engagement in Langate. #LangateGraffiti #PublicArt #CommunityEngagement | Local? |
| qwen2.5:7b | Setting: Langate, 3/16, Sunny. Event: A building with graffiti on it.. Create a 100-word real-time report on this event.  | 100 |   0:35  | Real-Time Report - March 16, 2023. On the morning of March 16 in Langate, under sunny skies, attention was drawn to a recently renovated building adorned with vibrant graffiti art. The artwork showcases a variety of colorful patterns and abstract designs that seem to tell a story through bold strokes and creative expression. Locals have gathered around the mural, engaging in conversations about its meaning and significance to their community. The mayor has tweeted support for such artistic ventures, encouraging local artists to continue adding their voices to the city's cultural palette. This graffiti is not just an aesthetic addition but also a reflection of Langate’s vibrant and evolving cultural landscape. This report paints a vivid picture of the scene while aligning with typical real-time reporting practices, including immediate public reaction and official statements. | Local? |


| Model Name  | Prompt Length (Tokens) | Tokens Generated |  Time Taken (all models combined) (Minutes:Seconds) | Results |Notes      |
|-------------|------------------------|------------------|-----------------------|---------|-----------|
| qwen2.5:7b | Setting: Langate, 3/16, Partly Cloudy. Event: A crane in the background.. Create a 200-word real-time report on this event.  | 200 |   1:08  | Real-Time Report:Date and Time: March 16, 2023, 1:45 PM Location: Langate. Current Weather Conditions: Partly Cloudy, with an atmospheric temperature of 18°C (64°F) and a gentle northwesterly breeze. Event Description: At the construction site in Langate, a towering crane has been positioned prominently in the background. The sun is filtering through the clouds, casting a golden glow upon the structure that rises from the ground like a modernist skyscraper. Workers are bustling around, ensuring that each task is carried out flawlessly under the watchful eye of experienced professionals. The crane stands as a symbol of progress and advancement, its jib stretching skyward to connect with the building's skeletal framework. Nearby cranes offer a harmonious backdrop, creating an impressionist painting of industrious activity and human ingenuity in action. The air is filled with the hum of machinery and voices working together in perfect rhythm. Local residents are stopping to gaze at the scene, intrigued by this grand spectacle of construction and architectural marvel. Photographers are setting up their equipment, capturing moments that will become memories for years to come. The Langate community can take pride in witnessing firsthand how their city is growing and evolving before their eyes. | Local? |
| qwen2.5:7b | Setting: Langate, 3/16, Partly Cloudy. Event: AStrange amphibian builds a futuristic A canal with a lock... Create a 200-word real-time report on this event.  | 200 |   1:23  | **Real-Time Report: Strange Amphibian Canal Construction Observed in Langate, March 16** Date: March 16, 2023. Location: Langate, Cloudy but partly sunny conditions with occasional showers  . In a stunning display of unexplained natural phenomena, an amphibian species previously undocumented by local or global scientific communities has been observed constructing what appears to be a high-tech canal system capable of lock operations. This extraordinary discovery was made in the early morning hours at the edge of Langate's expansive marshlands. The alien-like creatures work tirelessly, using their intricate leg and tail structures to dig canals with precision that resembles advanced engineering techniques. Most remarkable is the presence of what appears to be a rudimentary canal lock system, something typically associated with human infrastructure developments rather than natural amphibian behavior. Local authorities and researchers from the nearby city science institute have been tasked with investigating this unprecedented event. Speculation ranges widely—from a previously unknown species exhibiting unusually complex behaviors due to an as-yet unexplained evolutionary leap—hypotheses that suggest advanced intelligence beyond current scientific understanding in the animal kingdom. Eyewitnesses report that these creatures seem to communicate intricately during construction and operate in groups, moving equipment and materials with astonishing efficiency. Further analysis is needed to understand how this amphibian species has acquired such abilities and why it chose this specific location for its endeavors. This unique event underscores the need for more comprehensive research into the natural world and challenges our current understanding of biological capabilities. Science and local communities across Langate are keeping a close eye on developments to better comprehend this extraordinary occurrence. For updates and further information, stay tuned. | Local?, using the event generator |
| qwen2.5:7b | Setting: Langate, 3/17, Very Cloudy. Event: Anot so secret disposal company eats a mysterious A boat with a red light on it... Create a 200-word real-time report on this event.  | 200 |   1:08  | Real-Time Report: Monday, March 17, 2020 - Langate Weather Conditions: Very Cloudy; Visibility Low. Just witnessed an unusual incident near the harbor of Langate around midday today (3/17). Sources indicate that a company identified as "Anot so secret disposal," known in local circles for its opaque operations, has discreetly acquired and apparently abandoned or disposed of a mysterious boat with red lights attached to it. This activity caught attention due to the unusual sequence of events: Initially, a solitary individual approached in what appeared to be a skiff bearing multiple red navigation lights but lacking any clear markings on the sides. The vessel was observed slowly moving towards the disposal company's facility before disappearing into its premises without further ado. Witnesses noted no other vessels or personnel responding to this boat’s presence during its transit. Local law enforcement and maritime authorities have been alerted, and they are currently investigating the situation for any illicit activities or breaches of environmental regulations. The red lights on the craft remain a pertinent detail, drawing comparisons to navigational beacons but under suspicious circumstances. Further statements pending as our coverage continues. Stay tuned for updates as authorities conduct their inquiries. End of Report | Local?, using the event generator |
| qwen2.5:7b | Setting: Langate, 3/17, Very Cloudy. Event: Acrazy duck builds a vibrant A boat with a red light on it... Create a 200-word real-time report on this event.  | 200 |   1:12  | Real-Time Report: March 17, 2023 - Langate, Cloudy In today's unusually atmospheric conditions of Langate—sufficiently overcast to dampen the usual brightness—Acrazy duck made a grand and whimsical appearance by constructing an eye-catching boat. Positioned with great craftsmanship, the boat boasts an unconventional yet charming feature: a vibrant red light that shines brightly against the gray skies. The event unfolded in the local harbor area where Acrazy duck, known for its creative endeavors, began assembling what seemed initially like any ordinary wooden structure. As onlookers gathered to observe this unique project, it gradually became clear why locals and passersby alike were intrigued by the sight. At heart, the boat serves as a functional vessel but takes on an artistic personality with the addition of the red light. This feature not only illuminates the surroundings under the cloudy sky, providing a stark contrast but also adds to the mystical charm. As the sun's rays attempt to break through the clouds, the red hue contrasts dramatically, creating a magical effect that transforms the ordinary day into something enchanting. The presence of Acrazy duck in this creative display sparked discussions among residents about resilience and innovation, inspiring others to consider how they can add brightness to their days through small acts of creativity. The vibrant boat with its illuminating light in Langate on March 17th has become a symbol of hope and the beauty that can emerge from unexpected places. | Local?, using the event generator |
| qwen2.5:7b | Setting: Langate, 3/26, Partly Cloudy. Event: Amajor paints a dark A computer monitor with a blue screen... Create a 200-word real-time report on this event.  | 200 |   1:14  | Real-Time Report: Major Paints Over a Darkened Computer Monitor (Blue Screen Incident) Date: 3/26; Location: Langate As of today, March 26th, skies over Langate were partly cloudy, providing a mellow backdrop to an unusual event unfolding in the neighborhood. At around 10:45 AM local time, residents witnessed an intriguing spectacle: a man identified as Major was seen painting directly on the surface of a darkened computer monitor showing a blue screen. The action, observed by a few neighbors initially reported as vandalism, has now been reassessed upon closer inspection. It appeared that rather than causing damage or criminal acts, Major had meticulously applied his brush and paint to transform the static blue screen into an artwork. The canvas was large and professional-grade paints were used, indicating a deliberate artistic endeavor. Local authorities have arrived on scene and are in conversation with Major, who expressed a desire to share this unique form of digital-to-analog collaboration with the community. They are considering the incident as an art installation, pending further review by local cultural boards. As of now, while the exact nature and purpose remain unclear, the event has sparked curiosity among passersby and social media users alike, potentially heralding a new wave of boundary-pushing artistic expression in digitally saturated environments. | Local, using the event generator, shaky image  |
